In [31]:
%matplotlib inline
import matplotlib.pyplot as plt
import io, base64, os, json, re
import pandas as pd
import numpy as np
from datetime import datetime, date, timedelta
from random import randint
from alive_progress import alive_bar

In [3]:
aapl_df = pd.read_csv('../stock/AAPL.csv')
selected_features = ['Date', 'Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume']
aapl_df = aapl_df[selected_features]

aapl_df.head()

Date       Open       High        Low      Close  \
0  2017-01-03 00:00:00-05:00  28.950001  29.082500  28.690001  29.037500   
1  2017-01-04 00:00:00-05:00  28.962500  29.127501  28.937500  29.004999   
2  2017-01-05 00:00:00-05:00  28.980000  29.215000  28.952499  29.152500   
3  2017-01-06 00:00:00-05:00  29.195000  29.540001  29.117500  29.477501   
4  2017-01-09 00:00:00-05:00  29.487499  29.857500  29.485001  29.747499   

   Adj Close     Volume  
0  27.174755  115127600  
1  27.144337   84472400  
2  27.282379   88774400  
3  27.586529  127007600  
4  27.839207  134247600

In [ ]:
aapl_df['Date'] = pd.to_datetime(aapl_df['Date'], utc=True)
aapl_df['Date'] = aapl_df['Date'].dt.date

In [4]:
# take random sets of sequential rows 
new_set = []
with alive_bar(total=100000, title='Updating') as bar:
    for row_set in range(0, 100000):
        if row_set%2000==0: print(row_set)
        row_quant = randint(10, 30)
        row_start = randint(0, len(aapl_df)-row_quant)
        market_subset = aapl_df.iloc[row_start:row_start+row_quant]

        Close_Date = max(market_subset['Date'])
        if row_set%2000==0: print(Close_Date)
        
        # Close_Gap = (market_subset['Close'] - market_subset['Close'].shift(1)) / market_subset['Close'].shift(1)
        Close_Gap = market_subset['Close'].pct_change()
        High_Gap = market_subset['High'].pct_change()
        Low_Gap = market_subset['Low'].pct_change() 
        Volume_Gap = market_subset['Volume'].pct_change() 
        Daily_Change = (market_subset['Close'] - market_subset['Open']) / market_subset['Open']
        Outcome_Next_Day_Direction = (market_subset['Volume'].shift(-1) - market_subset['Volume'])
        
        new_set.append(pd.DataFrame({'Sequence_ID':[row_set]*len(market_subset),
                                'Close_Date':[Close_Date]*len(market_subset),
                            'Close_Gap':Close_Gap,
                            'High_Gap':High_Gap,
                            'Low_Gap':Low_Gap,
                            'Volume_Gap':Volume_Gap,
                            'Daily_Change':Daily_Change,
                            'Outcome_Next_Day_Direction':Outcome_Next_Day_Direction}))
        bar()


0
2017-10-10 00:00:00-04:00
2000
2017-09-25 00:00:00-04:00
4000
2018-04-18 00:00:00-04:00
6000
2017-04-24 00:00:00-04:00
8000
2017-09-26 00:00:00-04:00
10000
2017-10-09 00:00:00-04:00
12000
2017-12-01 00:00:00-05:00
14000
2018-06-21 00:00:00-04:00
16000
2018-03-12 00:00:00-04:00
18000
2017-12-15 00:00:00-05:00
20000
2017-05-25 00:00:00-04:00
22000
2018-11-27 00:00:00-05:00
24000
2017-06-22 00:00:00-04:00
26000
2017-10-18 00:00:00-04:00
28000
2018-07-25 00:00:00-04:00
30000
2017-10-05 00:00:00-04:00
32000
2018-05-03 00:00:00-04:00
34000
2018-06-08 00:00:00-04:00
36000
2017-12-13 00:00:00-05:00
38000
2017-11-06 00:00:00-05:00
40000
2018-05-29 00:00:00-04:00
42000
2017-10-30 00:00:00-04:00
44000
2018-09-18 00:00:00-04:00
46000
2018-10-24 00:00:00-04:00
48000
2018-06-26 00:00:00-04:00
50000
2017-08-30 00:00:00-04:00
52000
2018-11-07 00:00:00-05:00
54000
2018-10-18 00:00:00-04:00
56000
2017-10-17 00:00:00-04:00
58000
2017-08-28 00:00:00-04:00
60000
2018-07-27 00:00:00-04:00
62000
2017-12-19

In [12]:
new_set

[     Sequence_ID                 Close_Date  Close_Gap  High_Gap   Low_Gap  \
 169            0  2017-10-10 00:00:00-04:00        NaN       NaN       NaN   
 170            0  2017-10-10 00:00:00-04:00  -0.001049 -0.007671 -0.000249   
 171            0  2017-10-10 00:00:00-04:00  -0.004015 -0.004602 -0.000997   
 172            0  2017-10-10 00:00:00-04:00  -0.016309 -0.006719 -0.011412   
 173            0  2017-10-10 00:00:00-04:00   0.018092  0.005585  0.008579   
 174            0  2017-10-10 00:00:00-04:00  -0.003963  0.011787 -0.007005   
 175            0  2017-10-10 00:00:00-04:00  -0.007522 -0.024396 -0.005417   
 176            0  2017-10-10 00:00:00-04:00  -0.008581 -0.003501  0.001140   
 177            0  2017-10-10 00:00:00-04:00   0.010109  0.009849 -0.000569   
 178            0  2017-10-10 00:00:00-04:00  -0.007568 -0.002920  0.000000   
 179            0  2017-10-10 00:00:00-04:00   0.000378 -0.004548  0.002785   
 180            0  2017-10-10 00:00:00-04:00  -0.016

In [13]:
len(market_subset)

17

In [17]:
new_set_df = pd.concat(new_set)
print(new_set_df.shape)
new_set_df = new_set_df.dropna(how='any') 
print(new_set_df.shape)

(1996895, 8)
(1796895, 8)


In [18]:
new_set_df.head()

Sequence_ID                 Close_Date  Close_Gap  High_Gap   Low_Gap  \
170            0  2017-10-10 00:00:00-04:00  -0.001049 -0.007671 -0.000249   
171            0  2017-10-10 00:00:00-04:00  -0.004015 -0.004602 -0.000997   
172            0  2017-10-10 00:00:00-04:00  -0.016309 -0.006719 -0.011412   
173            0  2017-10-10 00:00:00-04:00   0.018092  0.005585  0.008579   
174            0  2017-10-10 00:00:00-04:00  -0.003963  0.011787 -0.007005   

     Volume_Gap  Daily_Change  Outcome_Next_Day_Direction  
170   -0.265260     -0.004917                   1107200.0  
171    0.012784     -0.005121                  26732000.0  
172    0.304763     -0.013863                  11877200.0  
173    0.103780      0.006231                 160532800.0  
174    1.270810     -0.010762                -107226400.0

In [ ]:
# confirm sequence
# new_set_df[new_set_df['Close_Date'] == '1973-06-27'] {HLH, HLH, HHH, HHH, LLL, LML, LML, LLL, LHL, ...

In [19]:
# create sequences
# simplify the data by binning values into three groups
 
# Close_Gap
new_set_df['Close_Gap_LMH'] = pd.qcut(new_set_df['Close_Gap'], 3, labels=["L", "M", "H"])

# High_Gap - not used in this example
new_set_df['High_Gap_LMH'] = pd.qcut(new_set_df['High_Gap'], 3, labels=["L", "M", "H"])

# Low_Gap - not used in this example
new_set_df['Low_Gap_LMH'] = pd.qcut(new_set_df['Low_Gap'], 3, labels=["L", "M", "H"])

# Volume_Gap
new_set_df['Volume_Gap_LMH'] = pd.qcut(new_set_df['Volume_Gap'], 3, labels=["L", "M", "H"])
 
# Daily_Change
new_set_df['Daily_Change_LMH'] = pd.qcut(new_set_df['Daily_Change'], 3, labels=["L", "M", "H"])

# new set
new_set_df = new_set_df[["Sequence_ID", 
                         "Close_Date", 
                         "Close_Gap_LMH", 
                         "Volume_Gap_LMH", 
                         "Daily_Change_LMH", 
                         "Outcome_Next_Day_Direction"]]

new_set_df['Event_Pattern'] = new_set_df['Close_Gap_LMH'].astype(str) + new_set_df['Volume_Gap_LMH'].astype(str) + new_set_df['Daily_Change_LMH'].astype(str)

In [20]:
new_set_df.head()

Sequence_ID                 Close_Date Close_Gap_LMH Volume_Gap_LMH  \
170            0  2017-10-10 00:00:00-04:00             M              L   
171            0  2017-10-10 00:00:00-04:00             L              M   
172            0  2017-10-10 00:00:00-04:00             L              H   
173            0  2017-10-10 00:00:00-04:00             H              M   
174            0  2017-10-10 00:00:00-04:00             L              H   

    Daily_Change_LMH  Outcome_Next_Day_Direction Event_Pattern  
170                L                   1107200.0           MLL  
171                L                  26732000.0           LML  
172                L                  11877200.0           LHL  
173                H                 160532800.0           HMH  
174                L                -107226400.0           LHL

In [21]:
new_set_df['Outcome_Next_Day_Direction'].describe()

count    1.796895e+06
mean     1.452214e+05
std      5.071262e+07
min     -3.130984e+08
25%     -2.123960e+07
50%     -1.627200e+06
75%      1.791200e+07
max      2.785516e+08
Name: Outcome_Next_Day_Direction, dtype: float64

In [22]:
# reduce the set
compressed_set = new_set_df.groupby(['Sequence_ID', 
                                     'Close_Date'])['Event_Pattern'].apply(lambda x: "{%s}" % ', '.join(x)).reset_index()

print(compressed_set.shape)
compressed_set.head() 

(100000, 3)


Sequence_ID                 Close_Date  \
0            0  2017-10-10 00:00:00-04:00   
1            1  2018-01-19 00:00:00-05:00   
2            2  2018-03-05 00:00:00-05:00   
3            3  2017-07-31 00:00:00-04:00   
4            4  2018-06-12 00:00:00-04:00   

                                       Event_Pattern  
0  {MLL, LML, LHL, HMH, LHL, LLM, LLL, HHH, LLL, ...  
1      {HMH, LMM, MMM, MHH, HLM, HHH, LHL, HHH, MMM}  
2  {HHH, LLM, LLM, LML, HLM, HMH, HHH, LML, MML, ...  
3  {HMH, LHL, MLL, LLL, MHM, LHM, HLH, HMH, MMH, ...  
4  {LML, LML, HMM, MLL, HHH, MHL, MLM, LHM, MLM, ...

In [23]:
#compressed_outcomes = new_set_df[['Sequence_ID', 'Close_Date', 'Outcome_Next_Day_Direction']].groupby(['Sequence_ID', 'Close_Date']).agg()

compressed_outcomes = new_set_df.groupby(['Sequence_ID', 'Close_Date'])['Outcome_Next_Day_Direction'].mean()
compressed_outcomes = compressed_outcomes.to_frame().reset_index()
print(compressed_outcomes.shape)
compressed_outcomes.describe()

(100000, 3)


Sequence_ID  Outcome_Next_Day_Direction
count  100000.000000                1.000000e+05
mean    49999.500000                1.510543e+05
std     28867.657797                4.746988e+06
min         0.000000               -4.447480e+07
25%     24999.750000               -1.713183e+06
50%     49999.500000                6.705600e+04
75%     74999.250000                1.964033e+06
max     99999.000000                3.969355e+07

In [24]:
compressed_set = pd.merge(compressed_set, compressed_outcomes, on= ['Sequence_ID', 'Close_Date'], how='inner')
print(compressed_set.shape)
compressed_set.head()

(100000, 4)


Sequence_ID                 Close_Date  \
0            0  2017-10-10 00:00:00-04:00   
1            1  2018-01-19 00:00:00-05:00   
2            2  2018-03-05 00:00:00-05:00   
3            3  2017-07-31 00:00:00-04:00   
4            4  2018-06-12 00:00:00-04:00   

                                       Event_Pattern  \
0  {MLL, LML, LHL, HMH, LHL, LLM, LLL, HHH, LLL, ...   
1      {HMH, LMM, MMM, MHH, HLM, HHH, LHL, HHH, MMM}   
2  {HHH, LLM, LLM, LML, HLM, HMH, HHH, LML, MML, ...   
3  {HMH, LHL, MLL, LLL, MHM, LHM, HLH, HMH, MMH, ...   
4  {LML, LML, HMM, MLL, HHH, MHL, MLM, LHM, MLM, ...   

   Outcome_Next_Day_Direction  
0               -1.005783e+06  
1                3.895600e+06  
2               -8.271200e+06  
3               -4.066364e+05  
4               -9.009412e+04

In [25]:
# # reduce set 

# compressed_set = new_set_df.groupby(['Sequence_ID', 'Close_Date','Outcome_Next_Day_Direction'])['Event_Pattern'].apply(lambda x: "{%s}" % ', '.join(x)).reset_index()

compressed_set['Event_Pattern'] = [''.join(e.split()).replace('{','')
                                   .replace('}','') for e in compressed_set['Event_Pattern'].values]
compressed_set.head()

Sequence_ID                 Close_Date  \
0            0  2017-10-10 00:00:00-04:00   
1            1  2018-01-19 00:00:00-05:00   
2            2  2018-03-05 00:00:00-05:00   
3            3  2017-07-31 00:00:00-04:00   
4            4  2018-06-12 00:00:00-04:00   

                                       Event_Pattern  \
0  MLL,LML,LHL,HMH,LHL,LLM,LLL,HHH,LLL,MLL,LHL,LL...   
1                HMH,LMM,MMM,MHH,HLM,HHH,LHL,HHH,MMM   
2        HHH,LLM,LLM,LML,HLM,HMH,HHH,LML,MML,LHL,HLH   
3  HMH,LHL,MLL,LLL,MHM,LHM,HLH,HMH,MMH,MHM,HMH,HL...   
4  LML,LML,HMM,MLL,HHH,MHL,MLM,LHM,MLM,LHM,HLH,HH...   

   Outcome_Next_Day_Direction  
0               -1.005783e+06  
1                3.895600e+06  
2               -8.271200e+06  
3               -4.066364e+05  
4               -9.009412e+04

In [41]:
pd.to_datetime(compressed_set['Close_Date'][0]).strftime('%Y-%m-%d')

'2017-10-10'

In [57]:
compressed = datetime.strptime(pd.to_datetime(compressed_set['Close_Date'][0]).strftime('%Y-%m-%d'), '%Y-%m-%d')  \
                    - timedelta(days=90)

compressed = compressed.strftime('%Y-%m-%d')
type(compressed)

type(compressed_set['Close_Date'][0]), type(compressed)

compressed_set['Close_Date'] > compressed

0         True
1         True
2         True
3         True
4         True
         ...  
99995    False
99996    False
99997     True
99998     True
99999     True
Name: Close_Date, Length: 100000, dtype: bool

In [58]:
# use last x days of data for validation
compressed_set_validation = compressed_set[compressed_set['Close_Date'] >= compressed] # Sys.Date()-90 

compressed_set_validation.shape


(77055, 4)

In [59]:
list(compressed_set)

['Sequence_ID', 'Close_Date', 'Event_Pattern', 'Outcome_Next_Day_Direction']

In [60]:
# drop date field
compressed_set = compressed_set[['Sequence_ID', 'Event_Pattern','Outcome_Next_Day_Direction']]
compressed_set_validation = compressed_set_validation[['Sequence_ID', 'Event_Pattern','Outcome_Next_Day_Direction']]

In [61]:
compressed_set['Outcome_Next_Day_Direction'].describe()

count    1.000000e+05
mean     1.510543e+05
std      4.746988e+06
min     -4.447480e+07
25%     -1.713183e+06
50%      6.705600e+04
75%      1.964033e+06
max      3.969355e+07
Name: Outcome_Next_Day_Direction, dtype: float64

In [62]:
print(len(compressed_set['Outcome_Next_Day_Direction']))
len(compressed_set[abs(compressed_set['Outcome_Next_Day_Direction']) > 10000000])

100000


5130

In [63]:
# keep only keep big/interesting moves 
print('all moves:', len(compressed_set))
compressed_set = compressed_set[abs(compressed_set['Outcome_Next_Day_Direction']) > 10000000]
compressed_set['Outcome_Next_Day_Direction'] = np.where((compressed_set['Outcome_Next_Day_Direction'] > 0), 1, 0)
compressed_set_validation['Outcome_Next_Day_Direction'] = np.where((compressed_set_validation['Outcome_Next_Day_Direction'] > 0), 1, 0)
print('big moves only:', len(compressed_set))    

all moves: 100000
big moves only: 5130


In [64]:
compressed_set.head()

Sequence_ID                                    Event_Pattern  \
50           50                  HHH,MLM,MLH,HMH,HHH,MLH,MHH,MLM   
51           51  MMM,LMM,LLM,MHM,LHL,LLL,MML,LHL,LMH,MLM,MHM,LHL   
67           67              LHL,MLL,LML,MLH,MMM,LHL,HHH,HHH,HHH   
73           73              HMH,MLH,MLH,LML,MMH,HML,LMM,HMM,MLM   
94           94      LHL,HLH,LLL,HLM,MMM,MHH,MLL,LML,HMH,LHL,MLL   

    Outcome_Next_Day_Direction  
50                           0  
51                           1  
67                           0  
73                           0  
94                           0

In [65]:
# create two data sets - won/not won
compressed_set_pos = compressed_set[compressed_set['Outcome_Next_Day_Direction']==1][['Sequence_ID', 'Event_Pattern']]
print(compressed_set_pos.shape)
compressed_set_neg = compressed_set[compressed_set['Outcome_Next_Day_Direction']==0][['Sequence_ID', 'Event_Pattern']]
print(compressed_set_neg.shape)

(2673, 2)
(2457, 2)


In [66]:
flat_list = [item.split(',') for item in compressed_set['Event_Pattern'].values ]
unique_patterns = ','.join(str(r) for v in flat_list for r in v)
unique_patterns = list(set(unique_patterns.split(',')))
len(unique_patterns)

25

In [67]:
compressed_set['Outcome_Next_Day_Direction'].head()  

50    0
51    1
67    0
73    0
94    0
Name: Outcome_Next_Day_Direction, dtype: int64

In [68]:
# build the markov transition grid
def build_transition_grid(compressed_grid, unique_patterns):
    # build the markov transition grid

    patterns = []
    counts = []
    for from_event in unique_patterns:

        # how many times 
        for to_event in unique_patterns:
            pattern = from_event + ',' + to_event # MMM,MlM

            ids_matches = compressed_grid[compressed_grid['Event_Pattern'].str.contains(pattern)]
            found = 0
            if len(ids_matches) > 0:
                Event_Pattern = '---'.join(ids_matches['Event_Pattern'].values)
                found = Event_Pattern.count(pattern)
            patterns.append(pattern)
            counts.append(found)

    # create to/from grid
    grid_Df = pd.DataFrame({'pairs':patterns, 'counts': counts})

    grid_Df['x'], grid_Df['y'] = grid_Df['pairs'].str.split(',', 1).str
    grid_Df.head()

    grid_Df = grid_Df.pivot(index='x', columns='y', values='counts')

    grid_Df.columns= [col for col in grid_Df.columns]

    # del grid_Df.index.name

    # replace all NaN with zeros
    grid_Df.fillna(0, inplace=True)

    #grid_Df.rowSums(transition_dataframe) 
    grid_Df = grid_Df / grid_Df.sum(1)
    return (grid_Df)

grid_pos = build_transition_grid(compressed_set_pos, unique_patterns)
grid_neg = build_transition_grid(compressed_set_neg, unique_patterns)

/tmp/ipykernel_612/83166946.py:24: FutureWarning: Columnar iteration over characters will be deprecated in future releases.
  grid_Df['x'], grid_Df['y'] = grid_Df['pairs'].str.split(',', 1).str
/tmp/ipykernel_612/83166946.py:24: FutureWarning: Columnar iteration over characters will be deprecated in future releases.
  grid_Df['x'], grid_Df['y'] = grid_Df['pairs'].str.split(',', 1).str


In [69]:
grid_neg.head()

HHH       HHL  HHM       HLH  HLL       HLM       HMH  HML  HMM  \
x                                                                           
HHH  0.140651  0.035433  0.0  0.032569  0.0  0.314558  0.079234  0.0  0.0   
HHL  0.000000  0.000000  0.0  0.136258  0.0  0.000000  0.000000  0.0  0.0   
HHM  0.051376  0.000000  0.0  0.001662  0.0  0.000000  0.017607  0.0  0.0   
HLH  0.185008  0.000000  0.0  0.143902  0.0  0.332756  0.162610  0.0  0.0   
HLL  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.000000  0.0  0.0   

          LHL  ...       LMM  MHH       MHL  MHM       MLH  MLL       MLM  \
x              ...                                                          
HHH  0.052686  ...  0.000000  0.0  0.311688  0.0  0.250400  0.0  0.327327   
HHL  0.000000  ...  0.000000  0.0  0.000000  0.0  0.000000  0.0  0.000000   
HHM  0.000000  ...  0.000000  0.0  0.000000  0.0  0.000000  0.0  0.000000   
HLH  0.066370  ...  0.090141  0.0  0.974026  0.0  0.073145  0.0  0.042042   
HLL  0.000000  ...  0.000000  0.0  0.000000  0.0  0.000000  0.0  0.000000   

          MMH       MML       MMM  
x                                  
HHH  0.000000  0.000000  0.204218  
HHL  0.000000  0.000000  0.000000  
HHM  0.089489  0.000000  0.000000  
HLH  0.035511  0.250737  0.000000  
HLL  0.000000  0.000000  0.000000  

[5 rows x 25 columns]

In [70]:
grid_pos.head()

HHH  HHL       HHM       HLH  HLL       HLM       HMH  HML  \
x                                                                      
HHH  0.091240  1.0  0.122987  0.015564  0.0  0.060241  0.127077  0.0   
HHL  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000  0.0   
HHM  0.000000  0.0  0.000000  0.000000  0.0  0.095290  0.118768  0.0   
HLH  0.039669  0.0  0.112738  0.021012  0.0  0.000000  0.014174  0.0   
HLL  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000  0.0   

          HMM       LHL  ...  LMM       MHH       MHL  MHM       MLH  MLL  \
x                        ...                                                
HHH  0.000000  0.081637  ...  0.0  0.000000  0.033735  0.0  0.106476  0.0   
HHL  0.000000  0.000000  ...  0.0  0.000000  0.000000  0.0  0.000000  0.0   
HHM  0.121648  0.000000  ...  0.0  0.000000  0.000000  0.0  0.000000  0.0   
HLH  0.000000  0.036726  ...  0.0  0.151111  0.000000  0.0  0.000000  0.0   
HLL  0.000000  0.000000  ...  0.0  0.000000  0.000000  0.0  0.000000  0.0   

          MLM       MMH  MML       MMM  
x                                       
HHH  0.159683  0.000000  0.1  0.213626  
HHL  0.000000  0.000000  0.0  0.000000  
HHM  0.000000  0.183333  0.0  0.000000  
HLH  0.007258  0.201389  0.0  0.000000  
HLL  0.000000  0.000000  0.0  0.000000  

[5 rows x 25 columns]

In [ ]:
# compressed_set_validation[compressed_set_validation['Sequence_ID' == seq_id]]

In [71]:
def safe_log(x,y):
   try:
      lg = np.log(x/y)
   except:
      lg = 0
   return lg

# predict on out of sample data
actual = []
predicted = []
for seq_id in compressed_set_validation['Sequence_ID'].values:
    patterns = compressed_set_validation[compressed_set_validation['Sequence_ID'] == seq_id]['Event_Pattern'].values[0].split(',')
    pos = []
    neg = []
    log_odds = []
    
    for id in range(0, len(patterns)-1):
        # get log odds
        # logOdds = log(tp(i,j) / tn(i,j)
        if (patterns[id] in list(grid_pos) and patterns[id+1] in list(grid_pos) and patterns[id] in list(grid_neg) and patterns[id+1] in list(grid_neg)):
                
            numerator = grid_pos[patterns[id]][patterns[id+1]]
            denominator = grid_neg[patterns[id]][patterns[id+1]]
            if (numerator == 0 and denominator == 0):
                log_value =0
            elif (denominator == 0):
                log_value = np.log(numerator / 0.00001)
            elif (numerator == 0):
                log_value = np.log(0.00001 / denominator)
            else:
                log_value = np.log(numerator/denominator)
        else:
            log_value = 0
        
        log_odds.append(log_value)
        
        pos.append(numerator)
        neg.append(denominator)
      
    # print('outcome:', compressed_set_validation[compressed_set_validation['Sequence_ID']==seq_id]['Outcome_Next_Day_Direction'].values[0])
    # print(sum(pos)/sum(neg))
    # print(sum(log_odds))

    actual.append(compressed_set_validation[compressed_set_validation['Sequence_ID']==seq_id]['Outcome_Next_Day_Direction'].values[0])
    predicted.append(sum(log_odds))

from sklearn.metrics import confusion_matrix

confusion_matrix(actual, [1 if p > 0 else 0 for p in predicted])

outcome: 0
0.9983884255764163
-34.000195444664655
outcome: 1
2.106186265714904
20.509378093710765
outcome: 0
0.47151183825937504
-17.142661818490673
outcome: 0
1.3093670073599961
13.323508840960418
outcome: 0
6.382896511689499
57.429500304861584
outcome: 0
0.6668034446626123
-19.041112265912766
outcome: 0
1.4302505025632246
3.8747434736728223
outcome: 1
1.5599421939200109
19.438972326485896
outcome: 0
0.8291488021071366
16.386139246856906
outcome: 1
1.3462410899296489
-14.859931523049369
outcome: 0
1.3774558657026372
-11.676772904040456
outcome: 1
0.8082643702378144
13.120203789548135
outcome: 1
1.073052710886775
-34.221427552203394
outcome: 1
0.5192772835511961
5.118864892324263
outcome: 0
7.163140981993272
36.45919532036257
outcome: 0
0.8301440762164111
-19.928984096893416
outcome: 0
0.5807783890365389
13.47878535574886
outcome: 0
1.664542112496652
1.660332891380434
outcome: 0
0.9045517241799333
17.270975389435637
outcome: 1
0.8756257899052323
1.007868099831091
outcome: 1
0.621170371

/tmp/ipykernel_612/576167326.py:41: RuntimeWarning: divide by zero encountered in double_scalars
  print(sum(pos)/sum(neg))


outcome: 1
0.4405291411042103
-5.85838766316949
outcome: 0
0.5379492183820679
-14.284362063643336
outcome: 1
3.095725110469973
55.952468715313735
outcome: 0
0.7211028361558866
-0.32697352197065577
outcome: 1
1.1279434135692727
1.6763867686241438
outcome: 1
1.1354868814595598
-8.320800553408032
outcome: 1
1.0961272421934851
-0.616734583910391
outcome: 1
3.0865796757486015
28.034659311544875
outcome: 1
0.889816667801636
37.95396915977688
outcome: 0
5.095899148241017
69.35723522169702
outcome: 0
4.756911151349474
61.217520953527796
outcome: 0
3.4745947227975567
39.29673168947944
outcome: 0
0.6041957891643323
-19.50450135653301
outcome: 0
0.7947804255026044
-23.671312800649712
outcome: 0
0.8368167074160527
-28.50642911226722
outcome: 1
0.8220078026958563
2.699481919209654
outcome: 1
1.1851989737524444
-6.9130739801236585
outcome: 1
0.7362338665121428
-26.104840140951598
outcome: 1
0.7405049262786275
-18.570906057644248
outcome: 1
0.9703084008352847
7.403394676637673
outcome: 0
2.0862021100

array([[19422, 17027],
       [15695, 24911]])

In [ ]:
from sklearn.metrics import accuracy_score
score = accuracy_score(actual, [1 if p > 0 else 0 for p in predicted])
print('Accuracy:', round(score * 100,2), '%')

In [ ]:
import seaborn as sns
cm = confusion_matrix(actual, [1 if p > 0 else 0 for p in predicted])
fig, ax = plt.subplots(figsize=(5, 5))
sns.heatmap(cm, annot=True, ax = ax, fmt='g')

ax.set_title('Confusion Matrix') 
ax.set_xlabel('Predicted')
ax.set_ylabel('Actual')

ax.xaxis.set_ticklabels(['up day','down day'])
ax.yaxis.set_ticklabels(['up day','down day'])
ax.set_yticklabels(ax.get_yticklabels(), rotation = 0, fontsize = 8)
ax.set_xticklabels(ax.get_xticklabels(), rotation = 90, fontsize = 8)  
plt.show()